In [ ]:
def gs_clogit(Xbig,ybig,k,J,N,r1,r2,mu0,V0,tau,v,betadraw):
    
    %run functions/Clogit_lhf.ipynb  #evaluates lhf of the posterior kernel
    %run functions/Clogit_grad.ipynb #evaluates gradient of the posterior kernel
    %run functions/Clogit_hess.ipynb #evaluates hessian of the posterior kernel
    %run functions/mvt_rand.ipynb #draws from the mvt
    %run functions/kmvt_pdf.ipynb #to evaluate the mvt density
        
    
    R=r1+r2
    betamat = zeros([k,r2])  #will collect draws of beta
    accept=0 #will count MH acceptances

   
    thcount=1000 #will help us keep track of iterations
    #
    for i in range(1,R+1):
        #print(i)
        #
        #"range" doesn't consider last element, so R+1 gives us R draws
        #
        # draw betas
        #########################
        
        # without gradient or Hessian, just in case:
        ############################################
        #x0=betadraw
        #mle_out=minimize(Clogit_lhf,x0,args=(Xbig,ybig,k,J,N,mu0,V0),method='BFGS')
    
        # with gradient, but without Hessian - note switch to Newton method; a bit faster
        #################################################################################
        x0=betadraw
        mle_out=minimize(Clogit_lhf,x0,args=(Xbig,ybig,k,J,N,mu0,V0),method='Newton-CG',jac=Clogit_grad)
    
        # with gradient and (slow) Hessian
        ###################################
        #x0=betadraw
        #mle_out=minimize(Clogit_lhf,x0,args=(Xbig,ybig,k,J,N,mu0,V0),method='Newton-CG',jac=Clogit_grad,hess=Clogit_hess)
        # turned out to be too slow to be useful
         
        #Clogit_lhf: user-supplied lhf
        #x0: starting values
        #args(): elements to feed into the called functions
        #jac=Clogit_grad: user-supplied gradient
        #hess=Clogit_hess: user-supplied hessian
        #method: optimization method, here Newton-Conjugate Gradient
        
        #Get hessian at solution - need to run my hess function one more time
        #####################################################################
        
        bmax = mle_out.x  #will be a (k,) tuple, need to reshape
        Hmax=Clogit_hess(bmax,Xbig,ybig,k,J,N,mu0,V0)
        
        tmean = bmax
        tvcov = tau * inv(Hmax)
        
        # draw candidate beta
        betacan = mvt_rand(tmean, tvcov, v, 1) #k by 1
       
        
        # get MH portion for candidate draw
        ###################################
        # the following is the same as in Clogit_lhf
        int1=exp(Xbig @ betacan) #N*J by 1 - each row = xij'beta
        int2=(int1.reshape(N,J)).T #J by N - note reshape collects over rows first, so we first reshaped "the wrong way", then transposed
        #sum for each triplet
        denom = sum(int2,axis=0) #N by 1
        denom.shape=(1,N) #turn into a row vector
        f1=(ybig==1) #flag rows of ybig with chosen option
        f1=f1.reshape(int1.shape[0]) #need to reduce dimension for the next line
        num=int1[f1] #N by 1 - actual choices
        num.shape=(1,N)
        bigP=num/denom #element-by-element division, 1 by N, OK, max(bigP)<1 as required

        int3=sum(log(bigP))
        logcanbeta= -(1/2)*(betacan-mu0).T @ inv(V0) @ (betacan-mu0) + int3 - log(kmvt_pdf(betacan,tmean,tvcov,v))
    
        # get MH portion for current draw
        ###################################
        # the following is the same as in Clogit_lhf
        int1=exp(Xbig @ betadraw) #N*J by 1 - each row = xij'beta
        int2=(int1.reshape(N,J)).T #J by N - note reshape collects over rows first, so we first reshaped "the wrong way", then transposed
        #sum for each triplet
        denom = sum(int2,axis=0) #N by 1
        denom.shape=(1,N) #turn into a row vector
        f1=(ybig==1) #flag rows of ybig with chosen option
        f1=f1.reshape(int1.shape[0]) #need to reduce dimension for the next line
        num=int1[f1] #N by 1 - actual choices
        num.shape=(1,N)
        bigP=num/denom #element-by-element division, 1 by N, OK, max(bigP)<1 as required

        int3=sum(log(bigP))
        logdrawbeta= -(1/2)*(betadraw-mu0).T @ inv(V0) @ (betadraw-mu0) + int3 - log(kmvt_pdf(betadraw,tmean,tvcov,v))
        
        # get log of aceptance probability
        ###################################
        logacc = logcanbeta-logdrawbeta
                                                                                     
        # acceptance rule
        ##################
        lr = log(random.uniform(0,1))
                                                                                     
        if lr<logacc:
            betadraw=betacan
            accept = accept + 1                                                                                 
        
        if i>r1:
            betamat[:,(i-r1-1)] = squeeze(betadraw) # need to subtract 1 because indexing starts at zero
            # Note the "-1" since indexing starts at 0
        
        if i==thcount:
            print(i) #show iterations in increments of "thcount"
            thcount=thcount+1000   
            
    accept=accept/R;     
                  
    return(betamat,accept)